In [1]:
import pandas as pd, numpy as np, pickle
from quantfreedom.core.enums import FootprintCandlesTuple
from quantfreedom.indicators.tv_indicators import rsi_tv
import plotly.graph_objects as go
from quantfreedom.helpers.helper_funcs import np_lookback_one

candle_path = "../dbs/oct_dec_candles.pkl"

%load_ext autoreload
%autoreload 2

In [4]:
with open(candle_path, "rb") as f:
    oct_dec_candles: FootprintCandlesTuple = pickle.load(f)

In [5]:
rsi_length = 14
below_rsi_cur = 45
below_rsi_p = 30
below_rsi_pp = 35

In [15]:
rsi = rsi_tv(
    source=oct_dec_candles.candle_close_prices,
    length=rsi_length,
)

rsi = np.around(rsi, 1)

rsi_lb = np_lookback_one(
    arr=rsi,
    lookback=2,
    include_current=False,
    fill_value=np.nan,
    fwd_bwd="fwd",
)

p_rsi = rsi_lb[:, 0]
pp_rsi = rsi_lb[:, 1]

falling = pp_rsi > p_rsi
rising = rsi > p_rsi

is_below_cur = rsi < below_rsi_cur
is_below_p = p_rsi < below_rsi_p
is_below_pp = pp_rsi < below_rsi_pp

entries = is_below_cur & is_below_p & is_below_pp & falling & rising
entry_signals = np.where(entries, rsi, np.nan)

exit_prices = np.full_like(rsi, np.nan)

In [16]:
fig = go.Figure()
datetimes = oct_dec_candles.candle_open_datetimes

In [17]:
fig.add_scatter(
    x=datetimes,
    y=rsi,
    name="rsi",
    line_color="yellow",
)

In [18]:
fig.add_scatter(
    x=datetimes,
    y=entry_signals,
    mode="markers",
    name="entries",
    marker=dict(
        size=12,
        symbol="circle",
        color="#00F6FF",
        line=dict(
            width=1,
            color="DarkSlateGrey",
        ),
    ),
)

In [19]:
fig.add_hline(
    y=below_rsi_cur,
    opacity=0.3,
    line_color="red",
)

In [20]:
fig.update_layout(
    height=500,
    xaxis_rangeslider_visible=False,
    title=dict(
        x=0.5,
        text="Long Signals",
        xanchor="center",
        font=dict(
            size=50,
        ),
    ),
)